In [1]:
import numpy as np
import random
import math
from typing import Tuple, Literal, Union, Optional, List, Dict, NamedTuple, Callable, Any, Set
from queue import Queue
import warnings
import sys
import json
import time
import types
import pickle
import plotly.graph_objs as go
import plotly.express as px
import pandas as pd
import os
from eoh.problems.optimization.classic_benchmark_path_planning.utils.benchmark import MultiMapBenchmarker

In [2]:
pd.set_option('display.max_rows', None)     # 모든 행 표시
pd.set_option('display.max_columns', None)  # 모든 열 표시
pd.set_option('display.width', None)        # 가로 폭 제한 없음
pd.set_option('display.max_colwidth', None) # 셀 내용 잘림 없이 표시

In [3]:
class Map(NamedTuple):
    grid: np.ndarray
    start: Union[Tuple[float, float], Tuple[float, float, float]]
    goal: Union[Tuple[float, float], Tuple[float, float, float]]
    obstacles: List[Union[Tuple[float, float, float, float], Tuple[float, float, float, float, float, float]]] # x, y, width, height or x, y, z, width, height, dimension
    size: Union[Tuple[int, int], Tuple[int, int, int]]

class PlannerResult(NamedTuple):
    success: bool
    path: List[Union[Tuple[float, float], Tuple[float, float, float]]]
    nodes: List[Union[Tuple[float, float], Tuple[float, float, float]]]
    edges: List[Tuple[Tuple[float, ...], Tuple[float, ...]]]  # (parent, child)

class Node:
    def __init__(self, position, parent=None, cost=0.0):
        self.position = position
        self.parent = parent
        self.cost = cost
        self.children = []
        self.valid = True  # 장애물 충돌 여부 등


In [4]:
def visualize_map_shapes(
    map_array: np.ndarray,
    start: Optional[Tuple[int, ...]] = None,
    goal: Optional[Tuple[int, ...]] = None,
    obs:List[Tuple[int, ...]] = None,
    path: Optional[List[Tuple[float, ...]]] = None,
    nodes: Optional[List[Tuple[float, ...]]] = None,
    edges: Optional[List[Tuple[float, ...]]] = None,
    title: str = "Map Visualization"
):
    fig = go.Figure()

    if map_array.ndim == 2:
        height, width = map_array.shape
        
        for x, y, w, h in obs:
                fig.add_shape(
                    type="rect",
                    x0=x, x1=x+w, y0=y, y1=y+h,
                    fillcolor="purple",opacity=0.5,
                    line=dict(width=0)
                )

        # 방문 노드
        if nodes:
            vx, vy = zip(*nodes)
            fig.add_trace(go.Scatter(
                x=vx, y=vy, mode="markers",
                marker=dict(size=4, color="blue"),
                name="nodes"
            ))

        # 경로
        if path:
            px, py = zip(*path)
            fig.add_trace(go.Scatter(
                x=px, y=py, mode="lines+markers",
                line=dict(color="green"),
                marker=dict(size=6),
                name="Path"
            ))

        # 엣지 (연결 정보)
        if edges:
            for parent, child in edges:
                fig.add_trace(go.Scatter(
                    x=[parent.position[0], child.position[0]], y=[parent.position[1], child.position[1]],
                    mode="lines",
                    line=dict(color="lightblue", width=1),
                    showlegend=False,
                    hoverinfo="skip"
                ))


        # 시작/목표
        if start:
            fig.add_trace(go.Scatter(
                x=[start[0]], y=[start[1]], mode="markers",
                marker=dict(size=10, color="red"),
                name="Start"
            ))

        if goal:
            fig.add_trace(go.Scatter(
                x=[goal[0]], y=[goal[1]], mode="markers",
                marker=dict(size=10, color="orange"),
                name="Goal"
            ))

        fig.add_shape(
            type="rect",
            x0=0, y0=0,
            x1=width, y1=height,
            line=dict(color="white", width=3),
            fillcolor="rgba(0,0,0,0)",  # 투명 내부
            layer="above"
        )

        fig.update_layout(
            title=title,
            xaxis=dict(scaleanchor="y", showgrid=False),
            # yaxis=dict(showgrid=False, autorange="reversed"),
            yaxis=dict(showgrid=False),
            height=600, width=600
        )

    elif map_array.ndim == 3:
        z, y, x = map_array.nonzero()
        x, y, z = list(x), list(y), list(z)

        # for x,y,w,h in obs:
        #     fig.add_trace(go.Mesh3d(
        #         x=x, y=y, z=z,
        #         color='black',
        #         opacity=1.0,
        #         alphahull=0,
        #         name='Obstacles'
        #     ))

        fig.add_trace(go.Mesh3d(
            x=x, y=y, z=z,
            color='black',
            opacity=1.0,
            alphahull=0,
            name='Obstacles'
        ))

        if nodes:
            vx, vy, vz = zip(*nodes)
            fig.add_trace(go.Scatter3d(
                x=vx, y=vy, z=vz,
                mode='markers',
                marker=dict(size=2, color='blue'),
                name='Visited'
            ))

        # 엣지 (연결 정보)
        if edges:
            for parent, child in edges:
                fig.add_trace(go.Scatter3d(
                    x=[parent.position[0], child.position[0]],
                    y=[parent[1].position, child.position[1]],
                    z=[parent[2].position, child.position[2]],
                    mode='lines',
                    line=dict(color='lightblue', width=2),
                    showlegend=False,
                    hoverinfo="skip"
                ))

        if path:
            px_, py_, pz_ = zip(*path)
            fig.add_trace(go.Scatter3d(
                x=px_, y=py_, z=pz_,
                mode='lines+markers',
                marker=dict(size=3, color='green'),
                name='Path'
            ))

        if start:
            fig.add_trace(go.Scatter3d(
                x=[start[0]], y=[start[1]], z=[start[2]],
                mode='markers',
                marker=dict(size=5, color='red'),
                name='Start'
            ))

        if goal:
            fig.add_trace(go.Scatter3d(
                x=[goal[0]], y=[goal[1]], z=[goal[2]],
                mode='markers',
                marker=dict(size=5, color='orange'),
                name='Goal'
            ))

        fig.update_layout(
            title=title,
            scene=dict(aspectmode='data'),
            height=700, width=700
        )

        

    fig.show()


In [5]:
class MapIO:
    @staticmethod
    def save_map(map_data: Map, filename: str) -> None:
        """Save Map object to a binary file."""
        with open(filename, 'wb') as f:
            pickle.dump(map_data, f)

    @staticmethod
    def load_map(filename: str) -> Map:
        """Load Map object from a binary file."""
        if not os.path.exists(filename):
            raise FileNotFoundError(f"Map file not found: {filename}")
        with open(filename, 'rb') as f:
            return pickle.load(f)

In [6]:
raw_maps = ["Maze_map_easy.pkl", "Narrow_map.pkl", "Multi_obs_map.pkl"]

multi_obs_map = MapIO.load_map("Multi_obs_map.pkl")
print("Start:", multi_obs_map.start)
print("Obstacles:", len(multi_obs_map.obstacles))
print(multi_obs_map.grid.shape)

hard_maze_map = MapIO.load_map("Maze_map.pkl")
print("Start:", hard_maze_map.start)
print("Obstacles:", len(hard_maze_map.obstacles))
print(hard_maze_map.grid.shape)

maze_map = MapIO.load_map("Maze_map_easy.pkl")
print("Start:", maze_map.start)
print("Obstacles:", len(maze_map.obstacles))
print(maze_map.grid.shape)

narrow_map = MapIO.load_map("Narrow_map.pkl")
print("Start:", narrow_map.start)
print("Obstacles:", len(narrow_map.obstacles))
print(narrow_map.grid.shape)

Start: (1, 1)
Obstacles: 35
(100, 100)
Start: (29, 40)
Obstacles: 8
(100, 100)
Start: (29, 10)
Obstacles: 5
(100, 100)
Start: (80, 50)
Obstacles: 5
(100, 100)


In [38]:
maps=[multi_obs_map, maze_map, narrow_map]
# maps=[multi_obs_map, hard_maze_map, maze_map, narrow_map]

In [8]:
json_path = './eoh/src/eoh/problems/optimization/classic_benchmark_path_planning/utils/classic_method__.json'
with open(json_path, "r") as f:
    classic_method = json.load(f)

print(classic_method[0].keys())

dict_keys(['algorithm', 'algorithm_description', 'planning_mechanism', 'code'])


In [9]:
import_string ='''
from typing import Tuple, Literal, Union, Optional, List, Dict, NamedTuple, Callable, Any, Set, TYPE_CHECKING, Type
import time
from queue import Queue
import numpy as np
import random
import math
import sys
import os
from eoh.problems.optimization.classic_benchmark_path_planning.utils.architecture_utils import PlannerResult, Map
'''

In [ ]:
def get_exp_result(path, ref_avg):
    with open(path, "r") as f:
        data = json.load(f)
        filtered_sorted_algorithms = sorted(
        [alg for alg in data if alg.get('operator') != 'initial'],
        key=lambda x: x.get('objective', float('inf'))
        )

    len(filtered_sorted_algorithms)

    # ref_avg 앞에서 선언됨
    benchmarker = MultiMapBenchmarker(maps=maps, iter=100)

    g_total_df = pd.DataFrame()

    for method in filtered_sorted_algorithms:
        code_string = method['code']
        namedf = pd.DataFrame()
        namedf['alg_name'] = [method['objective']]* len(maps)
        with warnings.catch_warnings():
            warnings.simplefilter("ignore")
            planning_module = types.ModuleType("planning_module")
            exec(import_string+code_string, planning_module.__dict__)
            sys.modules[planning_module.__name__] = planning_module
            try:
                planner = planning_module.Planner(max_iter=5000)
            except:
                continue
            res, avg_rest = benchmarker.run(planner.plan)

            if avg_rest is None: continue
            imp_res = MultiMapBenchmarker.get_improvement(ref_avg, avg_rest)

            res_df = pd.concat([namedf, avg_rest, imp_res], axis=1)
            g_total_df = pd.concat([g_total_df, res_df], axis=0)

    return g_total_df

In [43]:
benchmarker = MultiMapBenchmarker(maps=maps, iter=100)

total_df = pd.DataFrame()

for method in classic_method:
    code_string = method['code']
    namedf = pd.DataFrame()
    namedf['alg_name'] = [method['algorithm']]* len(maps)
    with warnings.catch_warnings():
        warnings.simplefilter("ignore")
        planning_module = types.ModuleType("planning_module")
        exec(import_string+code_string, planning_module.__dict__)
        sys.modules[planning_module.__name__] = planning_module
        planner = planning_module.Planner(max_iter=5000)
        res, avg_rest = benchmarker.run(planner.plan)
        if method['algorithm'] == 'RRT':
            ref_avg = avg_rest
            
        if avg_rest is None: continue
        imp_res = MultiMapBenchmarker.get_improvement(ref_avg, avg_rest)

        res_df = pd.concat([namedf, avg_rest, imp_res], axis=1)
        total_df = pd.concat([total_df, res_df], axis=0)

total_df


[2025.09.17 - 15:47:25] Map 1
Iteration 1: Time taken: 0.0260 seconds, Success: True
Iteration 2: Time taken: 0.0229 seconds, Success: True
Iteration 3: Time taken: 0.0200 seconds, Success: True
Iteration 4: Time taken: 0.0220 seconds, Success: True
Iteration 5: Time taken: 0.0122 seconds, Success: True
Iteration 6: Time taken: 0.0115 seconds, Success: True
Iteration 7: Time taken: 0.0111 seconds, Success: True
Iteration 8: Time taken: 0.0509 seconds, Success: True
Iteration 9: Time taken: 0.0260 seconds, Success: True
Iteration 10: Time taken: 0.0577 seconds, Success: True
Iteration 11: Time taken: 0.0254 seconds, Success: True
Iteration 12: Time taken: 0.0251 seconds, Success: True
Iteration 13: Time taken: 0.0227 seconds, Success: True
Iteration 14: Time taken: 0.0850 seconds, Success: True
Iteration 15: Time taken: 0.0308 seconds, Success: True
Iteration 16: Time taken: 0.0171 seconds, Success: True
Iteration 17: Time taken: 0.0146 seconds, Success: True
Iteration 18: Time taken: 0

alg_name  map_id  success_rate  time_avg  num_nodes_avg  \
0                          RRT       0           1.0  0.035028         461.98   
1                          RRT       1           1.0  0.209557        1637.59   
2                          RRT       2           1.0  0.070956         859.41   
0                         RRT*       0           1.0  0.074324         447.98   
1                         RRT*       1           1.0  0.423035        1630.00   
2                         RRT*       2           1.0  0.127812         796.67   
0                  RRT-Connect       0           1.0  0.008656         106.12   
1                  RRT-Connect       1           1.0  0.015249         236.56   
2                  RRT-Connect       2           1.0  0.019704         251.01   
0                 RRT*-Connect       0           1.0  0.011739         129.62   
1                 RRT*-Connect       1           1.0  0.020041         263.17   
2                 RRT*-Connect       2           1.0  0.028765         288.33   
0                       BI-RRT       0           1.0  0.003126          72.90   
1                       BI-RRT       1           1.0  0.009301         228.86   
2                       BI-RRT       2           1.0  0.008329         163.75   
0                      BI-RRT*       0           1.0  0.019168          83.31   
1                      BI-RRT*       1           1.0  0.034966         240.33   
2                      BI-RRT*       2           1.0  0.030535         203.75   
0                Informed-RRT*       0           1.0  0.298898         726.89   
1                Informed-RRT*       1           1.0  0.360708        1218.83   
2                Informed-RRT*       2           1.0  0.188800         845.48   
0        Informed-RRT*-Connect       0           1.0  0.895766         471.14   
1        Informed-RRT*-Connect       1           1.0  0.446408         589.12   
2        Informed-RRT*-Connect       2           1.0  0.627521         563.16   
0  Bidirectional-Informed-RRT*       0           1.0  0.198690         440.85   
1  Bidirectional-Informed-RRT*       1           1.0  0.104017         508.97   
2  Bidirectional-Informed-RRT*       2           1.0  0.142080         551.00   
0        Improved-RRT*-Connect       0           1.0  0.143953         334.00   
1        Improved-RRT*-Connect       1           1.0  0.143147         644.38   
2        Improved-RRT*-Connect       2           1.0  0.147143         578.11   

   path_length_avg  smoothness_avg  success_improvement  time_improvement  \
0       188.080816        0.006254                  0.0         -0.000000   
1       303.968509        0.003852                  0.0         -0.000000   
2       150.713378        0.007887                  0.0         -0.000000   
0       157.771191        0.014527                  0.0       -112.181308   
1       225.665909        0.011059                  0.0       -101.870675   
2       116.530178        0.021042                  0.0        -80.128060   
0       195.985942        0.011055                  0.0         75.287648   
1       302.131675        0.007242                  0.0         92.723363   
2       160.833474        0.014351                  0.0         72.231338   
0       171.903015        0.016822                  0.0         66.486580   
1       258.288269        0.011071                  0.0         90.436318   
2       133.799123        0.021584                  0.0         59.460743   
0       179.646964        0.010684                  0.0         91.074891   
1       305.361103        0.006401                  0.0         95.561607   
2       156.816038        0.013011                  0.0         88.262427   
0       165.592398        0.018017                  0.0         45.277685   
1       264.277359        0.010454                  0.0         83.314143   
2       130.651560        0.022292                  0.0         56.966413   
0       149.971162        0.029144             

In [45]:
# classic method result
grouped_avg = total_df.groupby('alg_name').mean()
a = pd.DataFrame(grouped_avg)
a

map_id  success_rate  time_avg  num_nodes_avg  \
alg_name                                                                     
BI-RRT                          1.0           1.0  0.006919     155.170000   
BI-RRT*                         1.0           1.0  0.028223     175.796667   
Bidirectional-Informed-RRT*     1.0           1.0  0.148262     500.273333   
Improved-RRT*-Connect           1.0           1.0  0.144748     518.830000   
Informed-RRT*                   1.0           1.0  0.282802     930.400000   
Informed-RRT*-Connect           1.0           1.0  0.656565     541.140000   
RRT                             1.0           1.0  0.105181     986.326667   
RRT*                            1.0           1.0  0.208390     958.216667   
RRT*-Connect                    1.0           1.0  0.020182     227.040000   
RRT-Connect                     1.0           1.0  0.014536     197.896667   

                             path_length_avg  smoothness_avg  \
alg_name                                                       
BI-RRT                            213.941368        0.010032   
BI-RRT*                           186.840439        0.016921   
Bidirectional-Informed-RRT*       171.859631        0.029741   
Improved-RRT*-Connect             170.811093        0.030153   
Informed-RRT*                     161.982690        0.030676   
Informed-RRT*-Connect             165.450936        0.044705   
RRT                               214.254234        0.005997   
RRT*                              166.655759        0.015543   
RRT*-Connect                      187.996802        0.016492   
RRT-Connect                       219.650364        0.010883   

                             success_improvement  time_improvement  \
alg_name                                                             
BI-RRT                                       0.0         91.632975   
BI-RRT*                                      0.0         61.852747   
Bidirectional-Informed-RRT*                  0.0       -172.365749   
Improved-RRT*-Connect                        0.0       -128.880400   
Informed-RRT*                                0.0       -330.503418   
Informed-RRT*-Connect                        0.0      -1118.219344   
RRT                                          0.0          0.000000   
RRT*                                         0.0        -98.060014   
RRT*-Connect                                 0.0         72.127880   
RRT-Connect                                  0.0         80.080783   

                             node_improvement  length_improvement  \
alg_name                                                            
BI-RRT                              83.730304           -0.007719   
BI-RRT*                             81.194264           12.775225   
Bidirectional-Informed-RRT*         36.459870           19.815096   
Improved-RRT*-Connect               40.361656           19.889434   
Informed-RRT*                      -10.049902           23.838074   
Informed-RRT*-Connect               32.171246           22.505155   
RRT                                  0.000000            0.000000   
RRT*                                 3.598092           21.518749   
RRT*-Connect                        74.107393           11.617421   
RRT-Connect                         77.792148           -3.437853   

                             smoothness_improvement  objective_score  
alg_name                                                              
BI-RRT                                    67.326861        27.821895  
BI-RRT*                                  180.716786        27.124543  
Bidirectional-Informed-RRT*              389.512360       -37.873105  
Improved-RRT*-Connect                    394.092078       -24.760000  
Informed-RRT*                            415.824461       -82.769059  
Informed-RRT*-Connect                    634.562555      -318.789897  
RRT                                        0.000000         0.000000  
RRT*          

In [47]:
exp_path_dict = dict()
exp_path_dict['eoh'] = "./path_planning/exp_result/basic_eoh_from_ma.json"
exp_path_dict['expert'] = "./path_planning/mobj/results/pops/population_generation_9.json"
exp_path_dict['analysis'] = "./path_planning/mobj_analysis/results/pops/population_generation_15.json"
exp_path_dict['ma1'] = "./paper_result/interactive_multi_agent1/results/pops/population_generation_8.json"
exp_path_dict['ma2'] = "./paper_result/interactive_multi_agent2/results/pops/population_generation_10.json"
exp_path_dict['ma3'] = "./paper_result/interactive_multi_agent3/results/pops/population_generation_15.json"
exp_path_dict['ma4'] = "./paper_result/interactive_multi_agent4/results/pops/population_generation_15.json"
exp_path_dict['ma5'] = "./paper_result/interactive_multi_agent5/results/pops/population_generation_23.json"
exp_path_dict['ma6'] = "./paper_result/interactive_multi_agent_major_init/results/pops/population_generation_1.json"

In [48]:
result_dfs = {}

for k, path in exp_path_dict.items():
    res = get_exp_result(path, ref_avg)
    result_dfs[k] = res

[2025.09.17 - 15:56:48] Map 1
Iteration 1: Time taken: 0.0035 seconds, Success: True
Iteration 2: Time taken: 0.0095 seconds, Success: True
Iteration 3: Time taken: 0.0065 seconds, Success: True
Iteration 4: Time taken: 0.0140 seconds, Success: True
Iteration 5: Time taken: 0.0065 seconds, Success: True
Iteration 6: Time taken: 0.0075 seconds, Success: True
Iteration 7: Time taken: 0.0065 seconds, Success: True
Iteration 8: Time taken: 0.0050 seconds, Success: True
Iteration 9: Time taken: 0.0060 seconds, Success: True
Iteration 10: Time taken: 0.0091 seconds, Success: True
Iteration 11: Time taken: 0.0075 seconds, Success: True
Iteration 12: Time taken: 0.0088 seconds, Success: True
Iteration 13: Time taken: 0.0105 seconds, Success: True
Iteration 14: Time taken: 0.0092 seconds, Success: True
Iteration 15: Time taken: 0.0055 seconds, Success: True
Iteration 16: Time taken: 0.0050 seconds, Success: True
Iteration 17: Time taken: 0.0085 seconds, Success: True
Iteration 18: Time taken: 0

In [ ]:
# exp_path_dict['ma6'] = "./paper_result/interactive_multi_agent_major_init/results/pops/population_generation_1.json"
# res = get_exp_result(exp_path_dict['ma6'], ref_avg)
# result_dfs['ma6'] = res

[2025.09.17 - 15:46:24] Map 1
Iteration 1: Time taken: 0.0160 seconds, Success: True
Iteration 2: Time taken: 0.0253 seconds, Success: False
Iteration 3: Time taken: 0.0115 seconds, Success: True
Iteration 4: Time taken: 0.0186 seconds, Success: True
Iteration 5: Time taken: 0.0142 seconds, Success: True
Iteration 6: Time taken: 0.0102 seconds, Success: True
Iteration 7: Time taken: 0.0115 seconds, Success: True
Iteration 8: Time taken: 0.0220 seconds, Success: True
Iteration 9: Time taken: 0.0101 seconds, Success: True
Iteration 10: Time taken: 0.0539 seconds, Success: True
Iteration 11: Time taken: 0.0205 seconds, Success: True
Iteration 12: Time taken: 0.0125 seconds, Success: True
Iteration 13: Time taken: 0.0140 seconds, Success: True
Iteration 14: Time taken: 0.0529 seconds, Success: True
Iteration 15: Time taken: 0.0105 seconds, Success: True
Iteration 16: Time taken: 0.0170 seconds, Success: True
Iteration 17: Time taken: 0.0135 seconds, Success: True
Iteration 18: Time taken: 

TypeError: 'NoneType' object is not subscriptable

In [54]:
result_dfs.keys()

dict_keys(['eoh', 'expert', 'analysis', 'ma1', 'ma2', 'ma3', 'ma4', 'ma5', 'ma6'])

In [61]:
frames = list()
raw_frames = list()

for k, df in result_dfs.items():
    # grouped_df = df.groupby('alg_name', as_index=False).mean()
    grouped_df = df.groupby('alg_name').mean(numeric_only=True).reset_index()
    # grouped_df = grouped_df.reset_index()
    grouped_df['method'] = k
    frames.append(grouped_df)
    df['method'] = k
    raw_frames.append(df)

merged_df = pd.concat([a]+frames, ignore_index=True, axis=0)
raw_merged_df = pd.concat(raw_frames, ignore_index=True, axis=0)

In [62]:
a

map_id  success_rate  time_avg  num_nodes_avg  \
alg_name                                                                     
BI-RRT                          1.0           1.0  0.006919     155.170000   
BI-RRT*                         1.0           1.0  0.028223     175.796667   
Bidirectional-Informed-RRT*     1.0           1.0  0.148262     500.273333   
Improved-RRT*-Connect           1.0           1.0  0.144748     518.830000   
Informed-RRT*                   1.0           1.0  0.282802     930.400000   
Informed-RRT*-Connect           1.0           1.0  0.656565     541.140000   
RRT                             1.0           1.0  0.105181     986.326667   
RRT*                            1.0           1.0  0.208390     958.216667   
RRT*-Connect                    1.0           1.0  0.020182     227.040000   
RRT-Connect                     1.0           1.0  0.014536     197.896667   

                             path_length_avg  smoothness_avg  \
alg_name                                                       
BI-RRT                            213.941368        0.010032   
BI-RRT*                           186.840439        0.016921   
Bidirectional-Informed-RRT*       171.859631        0.029741   
Improved-RRT*-Connect             170.811093        0.030153   
Informed-RRT*                     161.982690        0.030676   
Informed-RRT*-Connect             165.450936        0.044705   
RRT                               214.254234        0.005997   
RRT*                              166.655759        0.015543   
RRT*-Connect                      187.996802        0.016492   
RRT-Connect                       219.650364        0.010883   

                             success_improvement  time_improvement  \
alg_name                                                             
BI-RRT                                       0.0         91.632975   
BI-RRT*                                      0.0         61.852747   
Bidirectional-Informed-RRT*                  0.0       -172.365749   
Improved-RRT*-Connect                        0.0       -128.880400   
Informed-RRT*                                0.0       -330.503418   
Informed-RRT*-Connect                        0.0      -1118.219344   
RRT                                          0.0          0.000000   
RRT*                                         0.0        -98.060014   
RRT*-Connect                                 0.0         72.127880   
RRT-Connect                                  0.0         80.080783   

                             node_improvement  length_improvement  \
alg_name                                                            
BI-RRT                              83.730304           -0.007719   
BI-RRT*                             81.194264           12.775225   
Bidirectional-Informed-RRT*         36.459870           19.815096   
Improved-RRT*-Connect               40.361656           19.889434   
Informed-RRT*                      -10.049902           23.838074   
Informed-RRT*-Connect               32.171246           22.505155   
RRT                                  0.000000            0.000000   
RRT*                                 3.598092           21.518749   
RRT*-Connect                        74.107393           11.617421   
RRT-Connect                         77.792148           -3.437853   

                             smoothness_improvement  objective_score  
alg_name                                                              
BI-RRT                                    67.326861        27.821895  
BI-RRT*                                  180.716786        27.124543  
Bidirectional-Informed-RRT*              389.512360       -37.873105  
Improved-RRT*-Connect                    394.092078       -24.760000  
Informed-RRT*                            415.824461       -82.769059  
Informed-RRT*-Connect                    634.562555      -318.789897  
RRT                                        0.000000         0.000000  
RRT*          

In [70]:
merged_df[merged_df['method']=='ma6'].sort_values(by='length_improvement', ascending=False)


map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
219     1.0      0.996667  0.210909     918.966667       164.347505   
223     1.0      0.943333  0.649623     976.030000       166.861665   
225     1.0      0.920000  0.600899     502.170000       167.862143   
224     1.0      0.913333  0.686577     929.480000       169.258811   
221     1.0      0.960000  0.208578     240.130000       170.806778   
226     1.0      0.923333  0.417468     301.683333       170.767076   
218     1.0      0.986667  0.254599     340.520000       172.141284   
210     1.0      1.000000  0.044518     188.413333       173.300691   
222     1.0      0.983333  0.306700     308.363333       174.133652   
212     1.0      0.963333  0.049771     281.233333       173.901619   
213     1.0      0.990000  0.069200     310.503333       174.079225   
209     1.0      0.963333  0.043603     231.976667       174.425944   
215     1.0      0.973333  0.049557     263.093333       174.927842   
216     1.0      0.970000  0.115251     601.206667       175.713775   
214     1.0      0.986667  0.040473     214.503333       177.900693   
211     1.0      0.980000  0.062184       2.000000       179.248858   
208     1.0      0.950000  0.031689     254.206667       179.521128   
220     1.0      0.983333  0.222691     272.530000       179.723688   
217     1.0      0.973333  0.133265     987.890000       182.877853   

     smoothness_avg  success_improvement  time_improvement  node_improvement  \
219        0.041723            -0.333333        -97.108373         10.441021   
223        0.071171            -5.666667       -595.254522          0.767854   
225        0.076996            -8.000000       -678.845424         46.916560   
224        0.092684            -8.666667       -515.809595          7.184020   
221        0.066616            -4.000000       -209.847634         72.581287   
226        0.079101            -7.666667       -513.721470         65.669098   
218        0.075801            -1.333333       -230.401226         63.766610   
210        0.083584             0.000000         37.058815         79.645166   
222        0.050624            -1.666667       -273.780622         67.759690   
212        0.074519            -3.666667         33.677825         70.067258   
213        0.079090            -1.000000         10.347382         66.965199   
209        0.081369            -3.666667         40.231925         74.826445   
215        0.092052            -2.666667         31.919639         71.935864   
216        0.051449            -3.000000        -26.571539         37.645270   
214        0.081502            -1.333333         42.930339         76.826766   
211        0.060879            -2.000000         18.062968         99.737411   
208        0.076320            -5.000000         57.430521         72.394154   
220        0.029104            -1.666667       -208.568550         69.170012   
217        0.017057            -2.666667        -28.238795          2.103273   

     length_improvement  smoothness_improvement  objective_score   alg_name  \
219           22.701246              640.680198       -13.975030  112.66738   
223           21.179183             1174.143575      -188.331462  337.17753   
225           20.900360             1294.268834      -224.642067  482.54120   
224           20.123238             1533.640514      -178.334066  362.96059   
221           19.457386             1050.753404       -66.026092  150.07092   
226           19.283069             1339.550222      -174.182182  488.61260   
218           19.099229             1268.002057       -57.987486   59.81341   
210           18.388567             1448.949688        29.395533  -23.33681   
222           18.091522              787.080349       -75.677205  195.41050   
212           18.080859             1257.853580         8.907798   -4.10528   
213           18.057870             1350.508385        15.691479   -3.71940   
209           17.856230            

In [71]:
merged_df[merged_df['success_rate']>=1.0].sort_values(by='length_improvement', ascending=False)

map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
4       1.0           1.0  0.282802     930.400000       161.982690   
5       1.0           1.0  0.656565     541.140000       165.450936   
7       1.0           1.0  0.208390     958.216667       166.655759   
3       1.0           1.0  0.144748     518.830000       170.811093   
162     1.0           1.0  0.063596     333.410000       170.149248   
2       1.0           1.0  0.148262     500.273333       171.859631   
125     1.0           1.0  0.022621     222.823333       171.802445   
79      1.0           1.0  0.027854     200.053333       172.249447   
42      1.0           1.0  0.020108     178.890000       172.272975   
49      1.0           1.0  0.021592     188.423333       172.496103   
121     1.0           1.0  0.019887     201.826667       172.328341   
123     1.0           1.0  0.019827     209.756667       172.449503   
57      1.0           1.0  0.021027     184.626667       172.470598   
133     1.0           1.0  0.038399     210.623333       172.204986   
122     1.0           1.0  0.020258     207.730000       172.661390   
67      1.0           1.0  0.023906     187.256667       172.938728   
53      1.0           1.0  0.021048     179.606667       172.820324   
137     1.0           1.0  0.038587     182.093333       172.422268   
72      1.0           1.0  0.022806     190.270000       173.332603   
131     1.0           1.0  0.020267     210.430000       173.089159   
120     1.0           1.0  0.018749     198.183333       173.003572   
96      1.0           1.0  0.025672     223.000000       172.937805   
78      1.0           1.0  0.024050     198.916667       173.578301   
210     1.0           1.0  0.044518     188.413333       173.300691   
151     1.0           1.0  0.054215     208.520000       173.024828   
128     1.0           1.0  0.022737     174.113333       172.786613   
65      1.0           1.0  0.022965     182.773333       173.400960   
60      1.0           1.0  0.021288     183.200000       173.587014   
147     1.0           1.0  0.040415     221.450000       173.228831   
132     1.0           1.0  0.034511     208.053333       173.409424   
39      1.0           1.0  0.016219     186.743333       173.716691   
130     1.0           1.0  0.019896     204.806667       173.492348   
134     1.0           1.0  0.044009     199.006667       173.010644   
80      1.0           1.0  0.026750     190.596667       173.708830   
194     1.0           1.0  0.026368     200.010000       173.624689   
64      1.0           1.0  0.026769     197.566667       173.999257   
143     1.0           1.0  0.056271     191.386667       173.163225   
69      1.0           1.0  0.021395     182.686667       173.840769   
95      1.0           1.0  0.029043     230.943333       173.255399   
100     1.0           1.0  0.025724     245.320000       173.589445   
202     1.0           1.0  0.034579     199.613333       174.115880   
51      1.0           1.0  0.019852     179.670000       173.781344   
46      1.0           1.0  0.020386     187.816667       173.992295   
136     1.0           1.0  0.042420     230.653333       173.541009   
201     1.0           1.0  0.027549     203.043333       174.259721   
50      1.0           1.0  0.018348     190.186667       173.824895   
157     1.0           1.0  0.057075     240.906667       173.814935   
129     1.0           1.0  0.022873     182.713333       173.386955   
61      1.0           1.0  0.018853     179.866667       174.346756   
48      1.0           1.0  0.025688     237.686667       174.230273   
192     1.0           1.0  0.021182     182.300000       173.924949   
160     1.0           1.0  0.034301     225.100000       174.043268   
148     1.0           1.0  0.039715     185.560000       173.486266   
205     1.0           1.0  0.033232     193.080000       174.468061   
87      1.0           1.0  0.023500     218.713333       174.122320   
140     1.0           1.0  0.

In [25]:
raw_merged_df[raw_merged_df['map_id']==1].sort_values(by='objective_score', ascending=False)

alg_name  map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
448 -36.43867       1          1.00  0.022968         370.29       235.651696   
88   -6.33180       1          1.00  0.023003         283.44       237.711584   
337 -38.53073       1          1.00  0.022427         271.46       234.354771   
562 -33.96721       1          1.00  0.025985         205.25       236.202128   
331 -39.02046       1          1.00  0.021801         261.93       233.935687   
364 -35.51213       1          1.00  0.022485         265.38       235.581061   
334 -38.54314       1          1.00  0.023176         260.75       233.665943   
367 -35.47883       1          1.00  0.022166         269.57       234.869617   
385 -34.04928       1          1.00  0.021357         197.20       241.260555   
340 -38.01395       1          1.00  0.025639         290.50       234.096302   
349 -37.13607       1          1.00  0.025588         312.73       235.879855   
547 -37.48589       1          1.00  0.023193         217.90       234.759833   
343 -37.67647       1          1.00  0.026238         295.22       235.491473   
361 -35.65902       1          1.00  0.022857         267.40       235.265488   
352 -36.65222       1          1.00  0.023851         223.43       237.807524   
433 -29.96541       1          1.00  0.031352         262.32       235.391827   
388 -33.90720       1          1.00  0.026786         292.21       234.388157   
451 -36.26177       1          1.00  0.019717         278.74       234.833310   
439 -29.65900       1          1.00  0.033379         292.33       237.696705   
394 -33.51759       1          1.00  0.020730         234.23       234.479866   
454 -34.89579       1          1.00  0.031199         319.23       233.942429   
226 -35.41092       1          1.00  0.035104         364.50       237.179546   
499 -28.64627       1          1.00  0.033792         227.57       237.804329   
412 -32.08129       1          1.00  0.024385         275.56       233.025342   
379 -34.19888       1          1.00  0.026589         296.07       232.904517   
511 -24.54042       1          1.00  0.024423         171.34       240.134525   
397 -32.98846       1          1.00  0.032210         291.18       238.453228   
121 -27.62859       1          1.00  0.019188         230.69       236.047952   
565 -33.94541       1          1.00  0.025214         182.24       237.505879   
154 -26.35191       1          1.00  0.021562         238.50       237.854752   
139 -26.65888       1          1.00  0.017632         195.54       239.621382   
145 -26.55806       1          1.00  0.023193         233.42       239.546759   
112 -28.18988       1          1.00  0.020793         239.16       238.824856   
202 -25.04421       1          1.00  0.022946         297.33       239.009679   
199 -25.13323       1          1.00  0.020071         231.44       239.437783   
148 -26.54166       1          1.00  0.023858         238.06       238.287959   
175 -25.77476       1          1.00  0.018959         191.42       239.258532   
370 -35.05016       1          1.00  0.026201         281.63       231.038856   
160 -26.11907       1          1.00  0.021155         220.84       235.392987   
109 -28.86429       1          1.00  0.020351         228.53       236.468713   
196 -25.36826       1          1.00  0.022748         237.74       237.577279   
424 -31.40894       1          1.00  0.027866         243.81       232.278494   
442 -28.94013       1          1.00  0.031556         291.99       234.142778   
106 -29.37349       1          1.00  0.022429         229.37       239.185670   
124 -27.52708       1          1.00  0.023148         234.93       235.398456   
346 -37.37284       1          1.00  0.026016         287.02       231.054197   
142 -26.62690       1          1.00  0.021588         223.52       234.550233   
214 -24.75582       1          1.00  0.023575         228.78       237.358061   
184 -25.56803       1          1.00 